In [1]:
# Import the necessary library
import mysql.connector

# Establish a connection to MySQL
cnx = mysql.connector.connect(user='root', password='AasthaSuri22@', host='localhost')

# Create a cursor object
cursor = cnx.cursor()

# Create a new database
cursor.execute("CREATE DATABASE IF NOT EXISTS twitter_data_")

# Use the new database
cursor.execute("USE twitter_data_")

cursor.execute("SHOW Tables Like 'users';")
result = cursor.fetchone()

# Create a new table
create_table = """
CREATE TABLE IF NOT EXISTS users (
    id BIGINT PRIMARY KEY,
    name VARCHAR(100),
    screen_name VARCHAR(100),
    location VARCHAR(1000),
    followers_count INT,
    friends_count INT,
    statuses_count INT,
    utc_offset INT,
    time_zone VARCHAR(100),
    lang VARCHAR(100),
    following BOOLEAN,
    follow_request_sent BOOLEAN,
    notifications BOOLEAN,
    verified BOOLEAN,  
    protected BOOLEAN,  
    listed_countNT,  
    created_at TIMESTAMP  
)
"""

if result:
    cursor.execute("DROP Table users;")
    print("The Table Users already exists dropping the table........\n")
cursor.execute(create_table)
print("The Table User has been created")
# Close the cursor and connection
#cursor.close()
#cnx.close()

The Table User has been created


In [2]:
# Import necessary libraries
import json

# Initialize a set to store the IDs of tweets and users that have been seen
seen_tweets = set()
seen_users = set()

# Define the function to update metrics
def update_metrics(user):
    try:
        # Prepare the SQL query
        query = """
        UPDATE users
        SET statuses_count = statuses_count + 1
        WHERE id = %s
        """

        data = (user['id'],)

        # Execute the query
        cursor.execute(query, data)

        # Commit the transaction
        cnx.commit()
    except Exception as e:
        print(f"Error updating metrics: {e}")

In [3]:
import json

json_objects = []
with open("C:/Users/AASTHA/Desktop/RUTGERS BOOKS+Assignments/SEMESTER-2/Data Management/MAJOR PROJECT (TWITTER)/corona-out-2/corona-out-2", 'r') as f:
    for line in f:
        line = line.strip()  # remove leading/trailing white spaces
        if line:  # checks if line is not empty
            try:
                json_object = json.loads(line)
                json_objects.append(json_object)
            except json.JSONDecodeError as e:
                print(f"Error occurred: {e}")

# Now json_objects is a list of dictionaries that you can work with.
json_objects

[{'created_at': 'Sun Apr 12 18:27:25 +0000 2020',
  'id': 1249403767180668930,
  'id_str': '1249403767180668930',
  'text': 'RT @nuffsaidny: wishing death on people is weirdo behavior.',
  'source': '<a href="http://twitter.com/download/iphone" rel="nofollow">Twitter for iPhone</a>',
  'truncated': False,
  'in_reply_to_status_id': None,
  'in_reply_to_status_id_str': None,
  'in_reply_to_user_id': None,
  'in_reply_to_user_id_str': None,
  'in_reply_to_screen_name': None,
  'user': {'id': 1242817830946508801,
   'id_str': '1242817830946508801',
   'name': 'juwelz v',
   'screen_name': 'juwelz_v',
   'location': 'Lower East Side, Manhattan',
   'url': 'https://linktr.ee/juwelzv',
   'description': 'Event Lyfe LLC .. Brand Ambassador: #visionarysociety Music Manager: @ssizzzlee & @tmoneybeatsbang Production🎥📸 #BringNyCultureBack 🌊🌊🌊 !!',
   'translator_type': 'none',
   'protected': False,
   'verified': False,
   'followers_count': 43,
   'friends_count': 118,
   'listed_count': 0,
   

In [4]:
# Assuming json_objects is your list of tweet data
for data in json_objects:
    try:
        # If tweet has been seen before, ignore this tweet
        if data['id_str'] in seen_tweets:
            continue

        # Add the tweet ID to the set of seen tweets
        seen_tweets.add(data['id_str'])

        # Extract user information from the tweet
        user_info = data.get('user', {})

        # If user has not been seen before, add to user table
        if user_info.get('id') not in seen_users:
            # Prepare the SQL query
            query = """
                    INSERT INTO users (id, name, screen_name, location, followers_count, friends_count, 
                    statuses_count, utc_offset, time_zone, lang, following, follow_request_sent, notifications)
                    VALUES (%s, %s, %s, %s, %s, %s, %s, %s, %s, %s, %s, %s, %s)
                    """

            data = (user_info.get('id'), user_info.get('name'), user_info.get('screen_name'), 
                    user_info.get('location'), user_info.get('followers_count'), user_info.get('friends_count'), 
                    user_info.get('statuses_count'), user_info.get('utc_offset'), user_info.get('time_zone'), 
                    user_info.get('lang'), user_info.get('following'), user_info.get('follow_request_sent'), 
                    user_info.get('notifications'))

            # Execute the query
            cursor.execute(query, data)

            # Commit the transaction
            cnx.commit()

            # Add the user ID to the set of seen users
            seen_users.add(user_info['id'])

        # Update metrics for the user
        update_metrics(user_info)


    except Exception as e:
        # if there is an error loading the json of the tweet, print the error and skip
        print(f"Error processing line: {e}")
        continue

In [5]:
import re
from googletrans import Translator

def remove_unwanted_info(name):
    # Remove emojis
    name = re.sub("["
        u"\U0001F600-\U0001F64F"  # emoticons
        u"\U0001F300-\U0001F5FF"  # symbols & pictographs
        u"\U0001F680-\U0001F6FF"  # transport & map symbols
        u"\U0001F1E0-\U0001F1FF"  # flags (iOS)
        u"\U00002500-\U00002BEF"  # chinese char
        u"\U00002702-\U000027B0"
        u"\U00002702-\U000027B0"
        u"\U000024C2-\U0001F251"
        u"\U0001f926-\U0001f937"
        u"\U00010000-\U0010ffff"
        u"\u2640-\u2642" 
        u"\u2600-\u2B55"
        u"\u200d"
        u"\u23cf"
        u"\u23e9"
        u"\u231a"
        u"\ufe0f"  # dingbats
        u"\u3030"
                      "]+", '', name)

    # Remove phone numbers
    name = re.sub(r'\b\d{10}\b', '', name)

    # Remove hashtags
    name = re.sub(r'#\S+', '', name)

    return name

In [6]:
pip install pymysql googletrans==4.0.0-rc1

Note: you may need to restart the kernel to use updated packages.


In [7]:
!pip install pymysql

In [8]:
import pymysql
import re
import time

# Establish a connection to the database
db = pymysql.connect(host="localhost", user="root", password="AasthaSuri22@", database="twitter_data_")

# Create a cursor object
cursor = db.cursor()

# Execute SQL query to select all data from the table
cursor.execute("SELECT * FROM twitter_data_.users")

# Fetch all the rows
rows = cursor.fetchall()

max_retries = 5
for row in rows:
    # Clean the name (assuming the name is in the second column)
    name = row[1]
    
    # Remove all non-alphabet characters
    cleaned_name = re.sub(r'[^a-zA-Z]', ' ', name)

    for i in range(max_retries):
        try:
            # Update the name in the database
            cursor.execute(f"UPDATE users SET name='{cleaned_name}' WHERE id={row[0]}")
            db.commit()
            break
        except pymysql.err.OperationalError as e:
            if e.args[0] == 1205:  # Lock wait timeout exceeded
                wait = 5 * (i + 1)  # Exponential back-off
                print(f"Waiting for {wait} seconds before retrying.")
                time.sleep(wait)
                continue
            else:
                raise

# Disconnect from the server
db.close()

# Print a success message
print("The name column was successfully cleaned.")

The name column was successfully cleaned.


In [9]:
import mysql.connector

def find_users_most_followers():
    # This function finds users with the most followers
    connection = create_connection()
    cursor = connection.cursor()
    query = "SELECT * FROM table ORDER BY followers_count DESC LIMIT 10"
    cursor.execute(query)
    result = cursor.fetchall()
    return result

def find_users_most_friends():
    # This function finds users with the most friends (followings)
    connection = create_connection()
    cursor = connection.cursor()
    query = "SELECT * FROM table ORDER BY friends_count DESC LIMIT 10"
    cursor.execute(query)
    result = cursor.fetchall()
    return result

def find_users_most_liked_tweets():
    # This function finds users with the most liked tweets
    connection = create_connection()
    cursor = connection.cursor()
    query = "SELECT * FROM table ORDER BY favourites_count DESC LIMIT 10"
    cursor.execute(query)
    result = cursor.fetchall()
    return result

def find_users_most_tweets():
    # This function finds users with the most tweets
    connection = create_connection()
    cursor = connection.cursor()
    query = "SELECT * FROM table ORDER BY statuses_count DESC LIMIT 10"
    cursor.execute(query)
    result = cursor.fetchall()
    return result

def find_users_from_location(location):
    # This function finds users from a specific location
    connection = create_connection()
    cursor = connection.cursor()
    query = "SELECT * FROM table WHERE location = %s"
    cursor.execute(query, (location,))
    result = cursor.fetchall()
    return result

def find_users_starting_with_letter(letter):
    # This function finds users with names starting with a specific letter
    connection = create_connection()
    cursor = connection.cursor()
    query = "SELECT * FROM table WHERE name LIKE %s"
    cursor.execute(query, (letter + '%',))
    result = cursor.fetchall()
    return result

def find_users_with_screen_name(word):
    # This function finds users with screen names containing a specific word
    connection = create_connection()
    cursor = connection.cursor()
    query = "SELECT * FROM table WHERE screen_name LIKE %s"
    cursor.execute(query, ('%' + word + '%',))
    result = cursor.fetchall()
    return result


def find_user_by_id(user_id):
    # This function finds users with a specific ID
    connection = create_connection()
    cursor = connection.cursor()
    query = "SELECT * FROM table WHERE id = %s"
    cursor.execute(query, (user_id,))
    result = cursor.fetchall()
    return result

def account_with_most_friends():
    # This function finds the account with the most friends
    connection = create_connection()
    cursor = connection.cursor()
    query = "SELECT screen_name, friends_count FROM table ORDER BY friends_count DESC LIMIT 1"
    cursor.execute(query)
    result = cursor.fetchall()
    return result

def common_screen_name_by_location():
    # This function finds the most common screen name for each location
    connection = create_connection()
    cursor = connection.cursor()
    query = "SELECT location, screen_name, COUNT(*) AS frequency FROM table GROUP BY location, screen_name ORDER BY location, frequency DESC"
    cursor.execute(query)
    result = cursor.fetchall()
    return result
